# Imports

In [2]:
#Enable matplotlib to display in jupyter notebook & import it
%matplotlib inline

import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import folium
import os
from matplotlib import colors
from folium import plugins
from folium.plugins import FloatImage
import matplotlib.cm as cm
import branca



# Read in Data

In [3]:
listings = pd.read_pickle('data/listings_cleaned.pkl')
calendar = pd.read_pickle('data/calendar_cleaned.pkl')

# Hosts by Listings Count

In [6]:
#This map will colorcode listings based on how many other listing the host has in Boston

#create a map with our data in center
this_map = folium.Map([42.321145, -71.057083], zoom_start=12, tiles="Cartodb Positron", control_scale=True, prefer_canvas=True)

#add a legend to the map
LEGEND = 'https://raw.githubusercontent.com/collinreinking/BostonAirBnB/master/legend_1.png'
FloatImage(LEGEND, bottom=80, left=80).add_to(this_map)

#add a fullscreen button
folium.plugins.Fullscreen(
    position='topright',
    title='Full Screen',
    titleCancel='Exit Full Screen',
    forceSeparateButton=True).add_to(this_map)

#create a color dictionary for with custom buckets
buckets = [(1,2+1),(3,5+1),(6,10+1),(11,49+1),(50,136+1)]
color_names = ['blue','lightskyblue','limegreen','orange','red']
color_dict = {}
for n in range(len(buckets)):
    for m in range(buckets[n][0],buckets[n][1]):
        color_dict[m] = colors.to_hex(color_names[n])

#populate with the map listings, make pop up text=the number of other listings the host has
for n in listings.index:
    alist = listings.loc[n]
    plot_val = alist.calculated_host_listings_count
    popup_text = str(plot_val)
    folium.CircleMarker(weight=0, location=[alist.latitude, alist.longitude], radius=5,
    popup=popup_text, color=color_dict[plot_val],
    fill_color=color_dict[plot_val]).add_to(this_map)

#Save the map as an html file
this_map.save(os.path.join('Listings_Colored_by_Host_Listing_Count.html'))

this_map

In [11]:
#These tables help me see how many hosts have x number of listings.
#It also allows me to see exactly which hosts have a large number of listings,
#I can use the host_ids to look at their profile at https://www.airbnb.com/users/show/[host_id]
#I will also use this data later to make graphs of subsets of hosts based on volume of listings

host_counts = listings.groupby('host_id').calculated_host_listings_count.mean().value_counts().sort_index(ascending = False)
host_counts = pd.DataFrame(host_counts)
host_counts.index.names = ['Number_Of_Listings']
host_counts.columns = ['Number_of_Hosts_with_Number_of_Listings']
host_counts
host_count_id = listings.groupby('host_id').calculated_host_listings_count.mean()

host_counts['host_ids'] = host_counts.index.copy().map(lambda x: list(host_count_id[host_count_id == x].index))
host_counts['total_listings'] = host_counts.index * host_counts.Number_of_Hosts_with_Number_of_Listings
host_counts

Number_of_Hosts_with_Number_of_Listings  \
Number_Of_Listings                                            
136                                                       1   
79                                                        1   
61                                                        1   
58                                                        1   
50                                                        1   
25                                                        1   
24                                                        3   
20                                                        2   
19                                                        1   
17                                                        1   
15                                                        2   
14                                                        1   
13                                                        1   
12                                                        1   
11                                                        3   
10                                                        5   
9                                                         2   
8                                                         3   
7                                                        10   
6                                                        14   
5                                                        17   
4                                                        37   
3                                                        71   
2                                                       233   
1                                                      1768   

                                                             host_ids  \
Number_Of_Listings                                                      
136                                                        [30283594]   
79                                                            [25188]   
61                                                          [9419684]   
58                                                         [12243051]   
50                                                         [22348222]   
25                                                          [4962900]   
24                                      [1444340, 21184200, 26956083]   
20                                               [16186589, 32532791]   
19                                                           [814298]   
17                                                         [18202088]   
15                                                [9410008, 16442921]   
14                                                         [51673899]   
13                                                         [22541573]   
12                                                           [508268]   
11                                      [5618949, 28820575, 48494513]   
10                         [26988, 71783, 5578043, 8139434, 20857768]   
9                                                  [119019, 30489899]   
8                                       [3594203, 19246369, 19548932]   
7                   [324630, 2356643, 3137257, 4195134, 6608084, 1...   
6                   [8229, 1651480, 3637081, 6331373, 9189449, 965...   
5                   [50866, 85770, 255183, 1997048, 2006852, 30114...   
4                   [38440, 886871, 1407005, 1480518, 2355815, 318...   
3                   [128280, 212445, 434539, 522072, 847253, 84896...   
2                   [4240, 68870, 93916, 115522, 184232, 197327, 2...   
1                   [4804, 8021, 8061, 16701, 38997, 55603, 63525,...   

                    total_listings  
Number_Of_Listings                  
136                            136  
79                              79  
61                              61  
58                              58  
50                              50  
25                              25  
24                              72  
20           

# Top Lister Colored by price

In [15]:
#While we did not have space for these graphs in our presentation I believe they are interesting
#This graph will show all of the listings hosted by our top lister color coded by how expensive
#
place = 1

data = listings.copy()
data = listings[listings.host_id == host_counts.host_ids.iloc[place-1]]
plot_var = 'listed_price'

#map with our data in center
this_map = folium.Map([42.321145+.024, -71.057083-.03], zoom_start=13, tiles="Cartodb Positron")

#create a color dictionary for with custom buckets
norm = colors.Normalize(vmin=data[plot_var].min(), vmax=data[plot_var].max()*1.5)
colormap = lambda x : colors.to_hex(cm.brg(norm(x)))
color_dict = {p: colormap(p) for p in data[plot_var].unique()}

for n in data.index:
    alist = data.loc[n]
    plot_val = alist[plot_var]
    popup_text = str(alist.name)
    folium.CircleMarker(location=[alist.latitude, alist.longitude], radius=1,
    popup=popup_text, color=color_dict[plot_val],
    fill_color=color_dict[plot_val]).add_to(this_map)
this_map.fit_bounds(this_map.get_bounds())
this_map.save(os.path.join(str('lister_number_' + str(place) + '_by_volume.html')))
this_map

# 2nd lister by volume

In [17]:
#Same As above but for out second highest lister
place = 2

data = listings.copy()
data = listings[listings.host_id == host_counts.host_ids.iloc[place-1]]
plot_var = 'listed_price'
#map with our data in center
this_map = folium.Map([42.321145+.024, -71.057083-.03], zoom_start=13, tiles="Cartodb Positron")

#add some nice features to the map
folium.plugins.Fullscreen(
    position='topright',
    title='Full Screen',
    titleCancel='Exit Full Screen',
    forceSeparateButton=True).add_to(this_map)

#create a color dictionary for with custom buckets
norm = colors.Normalize(vmin=data[plot_var].min(), vmax=data[plot_var].max()*1.5)
colormap = lambda x : colors.to_hex(cm.brg(norm(x)))
color_dict = {p: colormap(p) for p in data[plot_var].unique()}

for n in data.index:
    alist = data.loc[n]
    plot_val = alist[plot_var]
    popup_text = str(alist.name)
    folium.CircleMarker(location=[alist.latitude, alist.longitude], radius=1.5,
    popup=popup_text, color=color_dict[plot_val],
    fill_color=color_dict[plot_val]).add_to(this_map)

this_map.save(os.path.join(str('lister_number_' + str(place) + '_by_volume.html')))

this_map

In [21]:
#Also cut for space this code creates fourmaps in one, these for maps represent our top four listers by volume

my_figure = branca.element.Figure()

my_maps = ['']*4

for place in range(1,5):
    data = listings[listings.host_id == host_counts.host_ids.iloc[place-1]]
    plot_var = 'listed_price'
    #map with our data in center
    my_maps[place-1] = folium.Map([42.321145+.024, -71.057083-.03], zoom_start=12, tiles="Cartodb Positron", control_scale=True)

    #create a color dictionary for with custom buckets
    norm = colors.Normalize(vmin=data[plot_var].min(), vmax=data[plot_var].max()*1.5)
    colormap = lambda x : colors.to_hex(cm.brg(norm(x)))
    color_dict = {p: colormap(p) for p in data[plot_var].unique()}

    for n in data.index:
        alist = data.loc[n]
        plot_val = alist[plot_var]
        popup_text = str(alist.name)
        folium.CircleMarker(location=[alist.latitude, alist.longitude], radius=1,
        popup=popup_text, color=color_dict[plot_val],
        fill_color=color_dict[plot_val]).add_to(my_maps[place-1])

#position the first map in the upper left
my_maps[0].position='absolute'
my_maps[0].left=(0,'%')
my_maps[0].width=(50.0,'%')
my_maps[0].height=(50.0,'%')

#position the second map in the upper right
my_maps[1].position='absolute'
my_maps[1].left=(50.0,'%')
my_maps[1].width=(50.0,'%')
my_maps[1].height=(50.0,'%')

#position the third map in the lower left
my_maps[2].position='absolute'
my_maps[2].left=(0.0,'%')
my_maps[2].width=(50.0,'%')
my_maps[2].height=(50.0,'%')
my_maps[2].top=(50.0,'%')

#position the fourth map in the lower right
my_maps[3].position='absolute'
my_maps[3].left=(50.0,'%')
my_maps[3].width=(50.0,'%')
my_maps[3].height=(50.0,'%')
my_maps[3].top=(50.0,'%')

#add all the maps to the figure
for num in range(4):
    my_figure.add_child(my_maps[num])
   

my_figure.save(os.path.join('top4byVolumeSideBySide.html'))

my_figure

# All hosts with 10 listings

In [22]:
#This code was my first attempt to create a map with multiply hosts, all of whom have the same number of listing
#the color coding now tries to give each host a different color
#the pop up when you click on a point now shows the host_id number

number_of_listings = 10
data = listings[listings.host_id.isin(host_counts.loc[number_of_listings].host_ids)]
plot_var = 'host_id'
#map with our data in center
this_map = folium.Map([42.321145+.024, -71.057083-.03], zoom_start=13, tiles="Cartodb Positron")

#add some nice features to the map
folium.plugins.Fullscreen(
    position='topright',
    title='Full Screen',
    titleCancel='Exit Full Screen',
    forceSeparateButton=True).add_to(this_map)

#create a color dictionary for with custom buckets
norm = colors.Normalize(vmin=data[plot_var].min(), vmax=data[plot_var].max()*2)
colormap = lambda x : colors.to_hex(cm.Set1(norm(x)))
color_dict = {p: colormap(p) for p in data[plot_var].unique()}

for n in data.index:
    alist = data.loc[n]
    plot_val = alist[plot_var]
    popup_text = str(alist.name)
    folium.CircleMarker(location=[alist.latitude, alist.longitude], radius=1.5,
    popup=popup_text, color=color_dict[plot_val],
    fill_color=color_dict[plot_val]).add_to(this_map)

this_map.save(os.path.join(str('all_hosts_with_'+'number_of_listings'+'_listings.html')))

this_map

# All Hosts with N listings

In [24]:
#This code creates a folder with a seperate map (in an html file) for each number of listings
#I used it to investigate if there were any patterns goegraphical in how midrange (by volume) hosts owned properties

if not os.path.exists('hosts_by_count/'):
    os.makedirs('hosts_by_count/')
    
for number_of_listings in list(host_counts.index):
    data = listings[listings.host_id.isin(host_counts.loc[number_of_listings].host_ids)]
    plot_var = 'host_id'
    #map with our data in center
    this_map = folium.Map([42.321145+.024, -71.057083-.03], zoom_start=13, tiles="Cartodb Positron")

    #add some nice features to the map
    folium.plugins.Fullscreen(
        position='topright',
        title='Full Screen',
        titleCancel='Exit Full Screen',
        forceSeparateButton=True).add_to(this_map)

    #create a color dictionary for with custom buckets
    norm = colors.Normalize(vmin=data[plot_var].min(), vmax=data[plot_var].max()*2)
    colormap = lambda x : colors.to_hex(cm.Set1(norm(x)))
    color_dict = {p: colormap(p) for p in data[plot_var].unique()}

    for n in data.index:
        alist = data.loc[n]
        plot_val = alist[plot_var]
        popup_text = str('listing_id='+str(alist.name) +'  +  host_id='+str(alist.host_id))
        folium.CircleMarker(location=[alist.latitude, alist.longitude], radius=1.5,
        popup=popup_text, color=color_dict[plot_val],
        fill_color=color_dict[plot_val]).add_to(this_map)


    this_map.save(os.path.join(str('hosts_by_count/' + 'all_hosts_with_' + str(number_of_listings) + '_listings.html')))
